# Build *Bacillus subtilis*

We will build an ME model from the NC_000913.2 Genbank file, the iJO1366
M model, and the complex reconstruction from iJL1678-ME

In [1]:
from __future__ import print_function, division, absolute_import

# python imports
import re
from os.path import join
from collections import defaultdict
import pickle

# third party imports
import pandas
import cobra

# COBRAme
import cobrame
from cobrame.util import building, mu, me_model_interface
from cobrame.io.json import save_json_me_model, save_reduced_json_me_model

# ECOLIme
import ecolime
from ecolime import (transcription, translation, flat_files, generics, formulas, compartments)
ecolime.__file__

'/home/jt/UCSD/bacillusme-master/ecolime/__init__.py'

## Part 1: Create minimum solveable ME-model
This will include the bare minimum representations of 
- Transcription Reactions
- Translation Reactions
- Complex Formation Reactions
- Metabolic Reactions

that still produce a working ME-model

### 1) Create Model Object and populate its global info
This includes important parameters that are used to calculate coupling 
constraints as well as organism-specific information such as peptide 
processing types

In [2]:
# Define Models
ijo_directory = join(flat_files.ecoli_files_dir, 'iYO844.json')
ijo = cobra.io.load_json_model(ijo_directory)
me = cobrame.MEModel('iYO844-ME')

# ME-models require special OptLang interface if cobrapy version >= 0.6.0
# If cannot import SymbolicParameter, assume using cobrapy
# versions <= 0.5.11
try:
    from optlang.interface import SymbolicParameter
except:
    pass
else:
    me.solver = me_model_interface

# "Translational capacity" of organism
me.global_info['kt'] = 4.5  # (in h-1)scott 2010, RNA-to-protein curve fit
me.global_info['r0'] = 0.087  # scott 2010, RNA-to-protein curve fit
me.global_info['k_deg'] = 1.0/5. * 60.0  # 1/5 1/min 60 min/h # h-1

# Molecular mass of RNA component of ribosome
me.global_info['m_rr'] = 1453. # in kDa

# Average molecular mass of an amino acid
me.global_info['m_aa'] = 109. / 1000.  # in kDa

# Proportion of RNA that is rRNA
me.global_info['f_rRNA'] = .86
me.global_info['m_nt'] = 324. / 1000.  # in kDa
me.global_info['f_mRNA'] = .02

# tRNA associated global information
me.global_info['m_tRNA'] = 25000. / 1000.  # in kDA
me.global_info['f_tRNA'] = .12

# Folding Properties
me.global_info['temperature'] = 37
me.global_info['propensity_scaling'] = .45

# DNA Replication Parameters
me.global_info['GC_fraction'] = 0.507896997096

# Define the types of biomass that will be synthesized in the model
me.add_biomass_constraints_to_model(["protein_biomass", "mRNA_biomass", "tRNA_biomass", "rRNA_biomass",
                                     "ncRNA_biomass", "DNA_biomass", "lipid_biomass", "constituent_biomass",
                                     "prosthetic_group_biomass", "peptidoglycan_biomass"])

# Define ME-model compartments
me.compartments = {"p": "Periplasm", "e": "Extra-organism", "c": "Cytosol", 
                   "im": 'Inner Membrane', 'om': "Outer Membrane", "mc": "ME-model Constraint",
                   "m": "Membrane"}

### 2) Load metabolites and build Metabolic reactions
The below reads in:
- Required 
 * **reaction_matrix.txt** (reaction matrix w/ reactions unlumped, metabolites renamed etc.)
 * **metabolites.txt** (metabolite properties)
 * **reactions.txt** (info on reversiblity, whether enzyme catalyzed etc.)
 * **m_to_me_mets.csv** (mapping of enzymes/complexes used in M-model to their ME-model compatible ID)
 * **protein_complexes.txt** (protein subunit stoichiometry of all complexes, used to identify metabolites as such)
 
It creates a new e coli M-model from this info then incorporates it into the ME-model using *add_m_model_content*. metabolites are added directly reactions are added as StoichiometricData

Metabolite types have different properties in an ME-model so enzyme complexes need added to the model as Complexes not Metabolites. Components in the E. coli M-model that are actually Complexes are compiled in *complex_list*

In [3]:
# m_model = flat_files.get_m_model()
m_model = flat_files.process_m_model(ijo, 'metabolites.txt',
                                     'm_to_me_mets.csv', 'reactions.txt',
                                     'reaction_matrix.txt',
                                     'protein_complexes.txt',
                                     defer_to_rxn_matrix={'GLUTRR', 'PAPSR'})
m_model.reactions.EX_glc__D_e.id = 'EX_glc__D_e'
m_model.repair()
# some of the "metabolites" in iJO1366 "M" model are actually complexes. We pass those in
# so they get created as complexes, not metabolites.
complexes = flat_files.get_complex_subunit_stoichiometry(
    'protein_complexes.txt').keys()
complex_set = set(
    [i.id for i in m_model.metabolites if i.id.split('_mod_')[0] in complexes])
building.add_m_model_content(me, m_model, complex_metabolite_ids=complex_set)

/home/jt/UCSD/bacillusme-master/ecolime/corrections.py:34 UserWarning: Creating new metabolite (4fe4s_c)
/home/jt/UCSD/bacillusme-master/ecolime/corrections.py:34 UserWarning: Creating new metabolite (2fe2s_c)
/home/jt/UCSD/bacillusme-master/ecolime/corrections.py:34 UserWarning: Creating new metabolite (LI_c)
/home/jt/UCSD/bacillusme-master/ecolime/corrections.py:34 UserWarning: Creating new metabolite (3a1hac1p_c)


In [4]:
# This adds exchange reactions for metabolites not contained in iJO1366
# Some of these cannot be produced by the model so they are added here
exchange_list = [
    'LI_c',
    'pqq_e',
    'cs_e',
    'tl_c',
    'RNase_m5','RNase_m16','RNase_m23'] # RNAses are gaps in model

for met_id in exchange_list:
    r = cobrame.MEReaction("EX_" + met_id)
    me.add_reaction(r)
    r.reaction = met_id + " <=> "

unknown metabolite 'pqq_e' created
unknown metabolite 'cs_e' created
unknown metabolite 'tl_c' created
unknown metabolite 'RNase_m5' created
unknown metabolite 'RNase_m16' created
unknown metabolite 'RNase_m23' created


In [5]:
last = 1;
reactionNumber = len(me.reactions);
for i in range(last,reactionNumber):
    rxn = me.reactions[i]
    print(i)
    print(rxn)
    print(rxn.reaction)

1
protein_biomass_to_biomass
protein_biomass --> biomass
2
mRNA_biomass_to_biomass
mRNA_biomass --> biomass
3
tRNA_biomass_to_biomass
tRNA_biomass --> biomass
4
rRNA_biomass_to_biomass
rRNA_biomass --> biomass
5
ncRNA_biomass_to_biomass
ncRNA_biomass --> biomass
6
DNA_biomass_to_biomass
DNA_biomass --> biomass
7
lipid_biomass_to_biomass
lipid_biomass --> biomass
8
constituent_biomass_to_biomass
constituent_biomass --> biomass
9
prosthetic_group_biomass_to_biomass
prosthetic_group_biomass --> biomass
10
peptidoglycan_biomass_to_biomass
peptidoglycan_biomass --> biomass
11
EX_2ddglcn_e
2ddglcn_e --> 
12
EX_2hxmp_e
2hxmp_e --> 
13
EX_2pg_e
2pg_e --> 
14
EX_2pglyc_e
2pglyc_e --> 
15
EX_3amba_e
3amba_e --> 
16
EX_3amp_e
3amp_e --> 
17
EX_3cmp_e
3cmp_e --> 
18
EX_3gmp_e
3gmp_e --> 
19
EX_3pg_e
3pg_e --> 
20
EX_3ump_e
3ump_e --> 
21
EX_4abut_e
4abut_e --> 
22
EX_5mtr_e
5mtr_e --> 
23
EX_6pgc_e
6pgc_e --> 
24
EX_Larab_e
Larab_e --> 
25
EX_Lcyst_e
Lcyst_e --> 
26
EX_abt__L_e
abt__L_e --> 
27
EX

### 3) Add Transcription and Translation 
The below reads in:
- Required
 * **NC_000913.2.gb** (Genbank sequence annotation)
 * **ecolime/translation.py** (codon to tRNA mapping)
- Optional
 * **TUs_from_ecocyc.txt** (TU definitions, start/stop positions, etc.)
 * **ecolime/translation.py** (dictionary of gene to frameshift mutation)
 
To construct the bare minimimum components of a transcription and translation reactions. For example, transcription reactions at this point include nucleotides and the synthesized RNAs.

In [6]:
gb_filename = join(flat_files.ecoli_files_dir,'NC_000964.gb')                                                                                    
tu_df = flat_files.get_tu_dataframe('TUs_from_bsubcyc.txt')

building.build_reactions_from_genbank(me, gb_filename, tu_df, verbose=False,
                                      frameshift_dict=translation.frameshift_dict,
                                      trna_to_codon=translation.trna_to_codon)



/home/jt/UCSD/cobrame-master/cobrame/core/reaction.py:852 UserWarning: RNA Polymerase () not found
/home/jt/UCSD/cobrame-master/cobrame/core/reaction.py:1093 UserWarning: ribosome not found
/home/jt/UCSD/cobrame-master/cobrame/core/reaction.py:1136 UserWarning: RNA_degradosome not found


In [7]:
last = i+1;
reactionNumber = len(me.reactions);
for i in range(last,reactionNumber):
    rxn = me.reactions[i]
    print(i)
    print(rxn)
    print(rxn.reaction)

247
transcription_TU8J2_1112_from_RpoD_mono
412 atp_c + 328 ctp_c + 332 gtp_c + 478 utp_c --> 1550 ppi_c
248
transcription_TU8J2_1243_from_RpoD_mono
154 atp_c + 111 ctp_c + 122 gtp_c + 186 utp_c --> 573 ppi_c
249
transcription_TU8J2_798_from_RpoD_mono
204 atp_c + 162 ctp_c + 116 gtp_c + 269 utp_c --> RNA_BSU_17900 + RNA_BSU_17910 + 211.50199622600002 mRNA_biomass + 751 ppi_c
250
transcription_TU8J2_569_from_RpoD_mono
963 atp_c + 641 ctp_c + 820 gtp_c + 812 utp_c --> 3236 ppi_c
251
transcription_TU8J2_1472_from_RpoD_mono
61 atp_c + 66 ctp_c + 47 gtp_c + 75 utp_c --> RNA_BSU_23040 + 79.159648349 mRNA_biomass + 249 ppi_c
252
transcription_TU8J2_1348_from_RpoD_mono
113 atp_c + 106 ctp_c + 104 gtp_c + 97 utp_c --> 420 ppi_c
253
transcription_TU8J2_9_from_RpoD_mono
523 atp_c + 471 ctp_c + 399 gtp_c + 637 utp_c --> RNA_BSU_33010 + RNA_BSU_33020 + 647.8763145739999 mRNA_biomass + 2030 ppi_c
254
transcription_TU8J2_348_from_RpoD_mono
120 atp_c + 122 ctp_c + 94 gtp_c + 138 utp_c --> RNA_BSU_3748

transcription_TU8J2_294_from_RpoD_mono
56 atp_c + 56 ctp_c + 43 gtp_c + 46 utp_c --> RNA_BSU_38790 + 64.250551961 mRNA_biomass + 201 ppi_c
748
transcription_TU8J2_1242_from_RpoD_mono
1261 atp_c + 786 ctp_c + 954 gtp_c + 938 utp_c --> 3939 ppi_c
749
transcription_TU8J2_7_from_RpoD_mono
146 atp_c + 134 ctp_c + 136 gtp_c + 178 utp_c --> RNA_BSU_34540 + 189.805111874 mRNA_biomass + 594 ppi_c
750
transcription_TU8J2_1019_from_RpoD_mono
424 atp_c + 343 ctp_c + 318 gtp_c + 352 utp_c --> RNA_BSU_07570 + 460.357805657 mRNA_biomass + 1437 ppi_c
751
transcription_TU8J2_589_from_RpoD_mono
48 atp_c + 52 ctp_c + 45 gtp_c + 71 utp_c --> RNA_BSU_28660 + 68.725621076 mRNA_biomass + 216 ppi_c
752
transcription_TU8J2_1471_from_RpoD_mono
20 atp_c + 30 ctp_c + 28 gtp_c + 60 utp_c --> RNA_BSU_22869 + 41.721087112 mRNA_biomass + 138 ppi_c
753
transcription_TU8J2_1251_from_RpoD_mono
112 atp_c + 115 ctp_c + 78 gtp_c + 133 utp_c --> RNA_BSU_11799 + RNA_BSU_11800 + RNA_BSU_11809 + 181.75014459300002 mRNA_biomass

transcription_TU8J2_1513_from_RpoD_mono
72 atp_c + 60 ctp_c + 58 gtp_c + 89 utp_c --> RNA_BSU_29910 + 89.003170819 mRNA_biomass + 279 ppi_c
980
transcription_TU8J2_836_from_RpoD_mono
2594 atp_c + 2431 ctp_c + 1906 gtp_c + 3040 utp_c --> RNA_BSU_15180 + RNA_BSU_15190 + RNA_BSU_15200 + RNA_BSU_15210 + RNA_BSU_15220 + RNA_BSU_15230 + RNA_BSU_15240 + RNA_BSU_15250 + RNA_BSU_15260 + RNA_BSU_15270 + 3020.1159516029993 mRNA_biomass + 9971 ppi_c
981
transcription_TU8J2_845_from_RpoD_mono
227 atp_c + 129 ctp_c + 147 gtp_c + 127 utp_c --> 630 ppi_c
982
transcription_TU8J2_2976_from_RpoD_mono
494 atp_c + 360 ctp_c + 377 gtp_c + 511 utp_c --> RNA_BSU_35080 + RNA_BSU_35090 + 551.006875602 mRNA_biomass + 1742 ppi_c
983
transcription_TU8J2_1510_from_RpoD_mono
103 atp_c + 93 ctp_c + 99 gtp_c + 152 utp_c --> RNA_BSU_29850 + 142.552079067 mRNA_biomass + 447 ppi_c
984
transcription_TU8J2_193_from_RpoD_mono
367 atp_c + 368 ctp_c + 278 gtp_c + 429 utp_c --> RNA_BSU_10940 + RNA_BSU_10950 + 460.226814206 mRN

159 atp_c + 108 ctp_c + 135 gtp_c + 111 utp_c --> 513 ppi_c
1313
transcription_TU8J2_57_from_RpoD_mono
1334 atp_c + 1166 ctp_c + 1092 gtp_c + 1384 utp_c --> RNA_BSU_38500 + RNA_BSU_38510 + RNA_BSU_38520 + RNA_BSU_38530 + RNA_BSU_38540 + 1558.521395335 mRNA_biomass + 4976 ppi_c
1314
transcription_TU8J2_669_from_RpoD_mono
1310 atp_c + 761 ctp_c + 958 gtp_c + 1162 utp_c --> 4191 ppi_c
1315
transcription_TU8J2_79_from_RpoD_mono
126 atp_c + 80 ctp_c + 69 gtp_c + 118 utp_c --> 393 ppi_c
1316
transcription_TU8J2_891_from_RpoD_mono
320 atp_c + 325 ctp_c + 233 gtp_c + 394 utp_c --> RNA_BSU_12420 + 404.30995361199996 mRNA_biomass + 1272 ppi_c
1317
transcription_TU8J2_90_from_RpoD_mono
231 atp_c + 194 ctp_c + 203 gtp_c + 299 utp_c --> RNA_BSU_29400 + 295.937691267 mRNA_biomass + 927 ppi_c
1318
transcription_TU8J2_1215_from_RpoD_mono
850 atp_c + 854 ctp_c + 734 gtp_c + 1140 utp_c --> RNA_BSU_00030 + RNA_BSU_00040 + RNA_BSU_00050 + RNA_BSU_00060 + 1112.152150092 mRNA_biomass + 3578 ppi_c
1319
trans

transcription_TU8J2_738_from_RpoD_mono
98 atp_c + 48 ctp_c + 54 gtp_c + 58 utp_c --> 258 ppi_c
1813
transcription_TU8J2_51_from_RpoD_mono
748 atp_c + 467 ctp_c + 625 gtp_c + 615 utp_c --> 2455 ppi_c
1814
transcription_TU8J2_2968_from_RpoD_mono
951 atp_c + 718 ctp_c + 873 gtp_c + 744 utp_c --> 3286 ppi_c
1815
transcription_TU8J2_129_from_RpoD_mono
563 atp_c + 451 ctp_c + 440 gtp_c + 480 utp_c --> 1934 ppi_c
1816
transcription_TU8J2_840_from_RpoD_mono
120 atp_c + 158 ctp_c + 105 gtp_c + 199 utp_c --> RNA_BSU_15090 + 184.310322922 mRNA_biomass + 582 ppi_c
1817
transcription_TU8J2_609_from_RpoD_mono
404 atp_c + 235 ctp_c + 291 gtp_c + 333 utp_c --> 1263 ppi_c
1818
transcription_TU8J2_1518_from_RpoD_mono
119 atp_c + 114 ctp_c + 126 gtp_c + 157 utp_c --> RNA_BSU_30520 + 165.010006536 mRNA_biomass + 516 ppi_c
1819
transcription_TU8J2_198_from_RpoD_mono
2873 atp_c + 2173 ctp_c + 2596 gtp_c + 2501 utp_c --> 10143 ppi_c
1820
transcription_TU8J2_1156_from_RpoD_mono
383 atp_c + 402 ctp_c + 341 gtp

...

RNA_BSU_05700 + 214.29517621500003 mRNA_biomass --> 
11109
DM_RNA_BSU_05730
RNA_BSU_05730 + 225.845635711 mRNA_biomass --> 
11110
DM_RNA_BSU_05740
RNA_BSU_05740 + 441.87610586899996 mRNA_biomass --> 
11111
DM_RNA_BSU_05760
RNA_BSU_05760 + 158.608584238 mRNA_biomass --> 
11112
DM_RNA_BSU_05770
RNA_BSU_05770 + 153.41341962299998 mRNA_biomass --> 
11113
DM_RNA_BSU_05780
RNA_BSU_05780 + 311.51153449799995 mRNA_biomass --> 
11114
DM_RNA_BSU_05800
RNA_BSU_05800 + 375.08749012699997 mRNA_biomass --> 
11115
DM_RNA_BSU_tRNA_79
RNA_BSU_tRNA_79 + 24.646002237000005 tRNA_biomass --> 
11116
DM_RNA_BSU_tRNA_80
RNA_BSU_tRNA_80 + 23.828596374 tRNA_biomass --> 
11117
DM_RNA_BSU_rRNA_30
RNA_BSU_rRNA_30 + 495.532147535 rRNA_biomass --> 
11118
DM_RNA_BSU_rRNA_12
RNA_BSU_rRNA_12 + 931.440514868 rRNA_biomass --> 
11119
DM_RNA_BSU_rRNA_13
RNA_BSU_rRNA_13 + 37.447219276999995 rRNA_biomass --> 
11120
DM_RNA_BSU_tRNA_21
RNA_BSU_tRNA_21 + 24.749039177000004 tRNA_biomass --> 
11121
DM_RNA_BSU_tRNA_22
RNA_BSU_tRNA

DM_RNA_BSU_14050
RNA_BSU_14050 + 275.872089201 mRNA_biomass --> 
11609
DM_RNA_BSU_14072
RNA_BSU_14072 + 164.869961019 mRNA_biomass --> 
11610
DM_RNA_BSU_14080
RNA_BSU_14080 + 174.729930929 mRNA_biomass --> 
11611
DM_RNA_BSU_14090
RNA_BSU_14090 + 389.599168184 mRNA_biomass --> 
11612
DM_RNA_BSU_14180
RNA_BSU_14180 + 225.954185331 mRNA_biomass --> 
11613
DM_RNA_BSU_14190
RNA_BSU_14190 + 358.62233742499996 mRNA_biomass --> 
11614
DM_RNA_BSU_14200
RNA_BSU_14200 + 77.89577438599999 mRNA_biomass --> 
11615
DM_RNA_BSU_14210
RNA_BSU_14210 + 256.605227364 mRNA_biomass --> 
11616
DM_RNA_BSU_14220
RNA_BSU_14220 + 173.196800223 mRNA_biomass --> 
11617
DM_RNA_BSU_14230
RNA_BSU_14230 + 142.274225527 mRNA_biomass --> 
11618
DM_RNA_BSU_14250
RNA_BSU_14250 + 306.848930946 mRNA_biomass --> 
11619
DM_RNA_BSU_14260
RNA_BSU_14260 + 190.97480263999998 mRNA_biomass --> 
11620
DM_RNA_BSU_14270
RNA_BSU_14270 + 324.73229010000006 mRNA_biomass --> 
11621
DM_RNA_BSU_14280
RNA_BSU_14280 + 412.58560715299996 mRNA_b

DM_RNA_BSU_21360
RNA_BSU_21360 + 240.909438319 mRNA_biomass --> 
12109
DM_RNA_BSU_21370
RNA_BSU_21370 + 837.2279615079999 mRNA_biomass --> 
12110
DM_RNA_BSU_21380
RNA_BSU_21380 + 261.179985962 mRNA_biomass --> 
12111
DM_RNA_BSU_21390
RNA_BSU_21390 + 615.6750303949999 mRNA_biomass --> 
12112
DM_RNA_BSU_21400
RNA_BSU_21400 + 262.344320365 mRNA_biomass --> 
12113
DM_RNA_BSU_21409
RNA_BSU_21409 + 69.79032085899999 mRNA_biomass --> 
12114
DM_RNA_BSU_21410
RNA_BSU_21410 + 352.314618224 mRNA_biomass --> 
12115
DM_RNA_BSU_21420
RNA_BSU_21420 + 67.44787083300001 mRNA_biomass --> 
12116
DM_RNA_BSU_21430
RNA_BSU_21430 + 84.88959412700001 mRNA_biomass --> 
12117
DM_RNA_BSU_21440
RNA_BSU_21440 + 142.750946847 mRNA_biomass --> 
12118
DM_RNA_BSU_21450
RNA_BSU_21450 + 402.312210109 mRNA_biomass --> 
12119
DM_RNA_BSU_21460
RNA_BSU_21460 + 130.960326314 mRNA_biomass --> 
12120
DM_RNA_BSU_21470
RNA_BSU_21470 + 673.2493493179999 mRNA_biomass --> 
12121
DM_RNA_BSU_21480
RNA_BSU_21480 + 54.108501411000006 m

RNA_BSU_28820 + 345.53467100599994 mRNA_biomass --> 
12775
DM_RNA_BSU_28840
RNA_BSU_28840 + 86.30711283 mRNA_biomass --> 
12776
DM_RNA_BSU_28850
RNA_BSU_28850 + 115.0189285 mRNA_biomass --> 
12777
DM_RNA_BSU_28860
RNA_BSU_28860 + 64.03083770100001 mRNA_biomass --> 
12778
DM_RNA_BSU_28870
RNA_BSU_28870 + 166.056177862 mRNA_biomass --> 
12779
DM_RNA_BSU_28900
RNA_BSU_28900 + 222.64573101600004 mRNA_biomass --> 
12780
DM_RNA_BSU_28910
RNA_BSU_28910 + 141.181245561 mRNA_biomass --> 
12781
DM_RNA_BSU_28920
RNA_BSU_28920 + 230.79607756599998 mRNA_biomass --> 
12782
DM_RNA_BSU_28930
RNA_BSU_28930 + 569.100317202 mRNA_biomass --> 
12783
DM_RNA_BSU_28950
RNA_BSU_28950 + 615.091060672 mRNA_biomass --> 
12784
DM_RNA_BSU_28960
RNA_BSU_28960 + 269.835344086 mRNA_biomass --> 
12785
DM_RNA_BSU_28970
RNA_BSU_28970 + 205.69045510200002 mRNA_biomass --> 
12786
DM_RNA_BSU_28980
RNA_BSU_28980 + 297.39019509599996 mRNA_biomass --> 
12787
DM_RNA_BSU_28990
RNA_BSU_28990 + 450.817433419 mRNA_biomass --> 
1278

RNA_BSU_35220 + 382.012599794 mRNA_biomass --> 
13324
DM_RNA_BSU_35240
RNA_BSU_35240 + 458.22261186300005 mRNA_biomass --> 
13325
DM_RNA_BSU_35250
RNA_BSU_35250 + 284.232904051 mRNA_biomass --> 
13326
DM_RNA_BSU_35260
RNA_BSU_35260 + 218.43613510699998 mRNA_biomass --> 
13327
DM_RNA_BSU_35270
RNA_BSU_35270 + 107.41622909899999 mRNA_biomass --> 
13328
DM_RNA_BSU_35280
RNA_BSU_35280 + 281.938107545 mRNA_biomass --> 
13329
DM_RNA_BSU_35290
RNA_BSU_35290 + 350.877704342 mRNA_biomass --> 
13330
DM_RNA_BSU_35300
RNA_BSU_35300 + 804.0250044260001 mRNA_biomass --> 
13331
DM_RNA_BSU_35310
RNA_BSU_35310 + 180.99575156999998 mRNA_biomass --> 
13332
DM_RNA_BSU_35319
RNA_BSU_35319 + 120.93290031799998 mRNA_biomass --> 
13333
DM_RNA_BSU_35320
RNA_BSU_35320 + 108.414660942 mRNA_biomass --> 
13334
DM_RNA_BSU_35330
RNA_BSU_35330 + 127.76196510199999 mRNA_biomass --> 
13335
DM_RNA_BSU_35340
RNA_BSU_35340 + 475.13645001699996 mRNA_biomass --> 
13336
DM_RNA_BSU_35350
RNA_BSU_35350 + 104.92118673 mRNA_biom

### 4) Add in complex Formation without modifications (for now)

The below reads in:
- Required
 * **protein_complexes.txt** (Metabolic complexes' protein subunit stoichiometries)
 * **protein_modification.txt** (Type and number of modifications for each protein)

In [8]:
# complex_stoichiometry_dict is a dict of {'complex_id': [{'bnum' : count}]}
rna_components = {"b3123", "b0455"} # component id should have 'RNA_ instead' of 'protein_'
# get Metabolic Complex composition from ECOLIme
complex_stoichiometry_dict = flat_files.get_complex_subunit_stoichiometry('protein_complexes.txt', rna_components)
# add complexes to model
complex_modification_dict = flat_files.get_complex_modifications('protein_modification.txt', 'protein_complexes.txt')
building.add_model_complexes(me, complex_stoichiometry_dict, complex_modification_dict, verbose=False)

# remove modifications. they will be added back in later
for data in me.complex_data:
    data.subreactions = {}
    
# add formation reactions for each of the ComplexDatas
for cplx_data in me.complex_data:
    formation = cplx_data.formation
    if formation:
        formation.update()
    else:
        cplx_data.create_complex_formation()

In [9]:
last = i+1;
reactionNumber = len(me.reactions);
for i in range(last,reactionNumber):
    rxn = me.reactions[i]
    print(i)
    print(rxn)
    print(rxn.reaction)

12539
formation_YmfC_mono
protein_b1135 --> YmfC_mono
12540
formation_CARNRACE-MONOMER
protein_b0036 --> CARNRACE-MONOMER
12541
formation_CPLX0-1601
protein_b1587 + protein_b1588 + protein_b1589 + protein_b1590 --> CPLX0-1601
12542
formation_CPLX0-1762
protein_b1388 + protein_b1389 + protein_b1390 + protein_b1392 --> CPLX0-1762
12543
formation_NANE-MONOMER
protein_b3223 --> NANE-MONOMER
12544
formation_DTDPGLUCDEHYDRAT2-MONOMER
protein_b3788 --> DTDPGLUCDEHYDRAT2-MONOMER
12545
formation_NARU-MONOMER
protein_b1469 --> NARU-MONOMER
12546
formation_YDGEF-CPLX
protein_b1599 + protein_b1600 --> YDGEF-CPLX
12547
formation_PHOSMANMUT-MONOMER
protein_b2048 --> PHOSMANMUT-MONOMER
12548
formation_CPLX0-3929
4.0 protein_b2708 --> CPLX0-3929
12549
formation_CPLX0-7652
4.0 protein_b3903 --> CPLX0-7652
12550
formation_ANSB-CPLX
4.0 protein_b2957 --> ANSB-CPLX
12551
formation_EG11983-MONOMER
protein_b2034 --> EG11983-MONOMER
12552
formation_NARW-MONOMER
protein_b1466 --> NARW-MONOMER
12553
formation_

formation_EG11591-MONOMER
protein_b0630 --> EG11591-MONOMER
13063
formation_ALTRODEHYDRAT-MONOMER
protein_b3091 --> ALTRODEHYDRAT-MONOMER
13064
formation_FUMARASE-A
2.0 protein_b1612 --> FUMARASE-A
13065
formation_RpsS_mono
protein_b3316 --> RpsS_mono
13066
formation_ABC-2-CPLX
2.0 protein_b1900 + protein_b1901 + 2.0 protein_b4460 --> ABC-2-CPLX
13067
formation_YAAJ-MONOMER
protein_b0007 --> YAAJ-MONOMER
13068
formation_CPLX0-7616
4.0 protein_b0509 --> CPLX0-7616
13069
formation_CPLX0-231
2.0 protein_b2092 + protein_b2093 + protein_b2094 + protein_b2415 + 2.0 protein_b2416 --> CPLX0-231
13070
formation_ABC-20-CPLX
protein_b3476 + protein_b3477 + protein_b3478 + protein_b3479 + protein_b3480 --> ABC-20-CPLX
13071
formation_Thr_RS_dim
2.0 protein_b1719 --> Thr_RS_dim
13072
formation_CPLX0-3141
2.0 protein_b3029 --> CPLX0-3141
13073
formation_NIRC-MONOMER
protein_b3367 --> NIRC-MONOMER
13074
formation_CPLX0-7811
4.0 protein_b3850 --> CPLX0-7811
13075
formation_EG11822-MONOMER
protein_b130

13729
formation_G6340-MONOMER
protein_b0614 --> G6340-MONOMER
13730
formation_2-DEHYDROPANTOATE-REDUCT-MONOMER
protein_b0425 --> 2-DEHYDROPANTOATE-REDUCT-MONOMER
13731
formation_ABC-46-CPLX
protein_b4227 + 2.0 protein_b4230 + protein_b4231 + protein_b4485 --> ABC-46-CPLX
13732
formation_PTSI-MONOMER
protein_b2416 --> PTSI-MONOMER
13733
formation_COADTRI-CPLX
6.0 protein_b3634 --> COADTRI-CPLX
13734
formation_CPLX0-3936
8.0 protein_b3058 --> CPLX0-3936
13735
formation_UDP-NACMURALGLDAPLIG-MONOMER
protein_b0085 --> UDP-NACMURALGLDAPLIG-MONOMER
13736
formation_CPLX0-7888
2.0 protein_b2290 --> CPLX0-7888
13737
formation_CPLX-171
2.0 protein_b0508 --> CPLX-171
13738
formation_CPLX0-1943
protein_b1252 + protein_b3005 + protein_b3006 + protein_b4291 --> CPLX0-1943
13739
formation_HISTCYCLOPRATPPHOS
protein_b2026 --> HISTCYCLOPRATPPHOS
13740
formation_LDC2-CPLX
10.0 protein_b0186 --> LDC2-CPLX
13741
formation_G7517-MONOMER
protein_b2920 --> G7517-MONOMER
13742
formation_CMPKI-MONOMER
protein_b

### 5) Add dummy reaction to model and unmodeled_protein_fraction

Includes the transcription, translation, complex_formation, and metabolic reaction. Sequence based on prevelance of each codon found in *E. coli*.
 - Required
     * [**codon_usage.csv**](http://openwetware.org/wiki/Escherichia_coli/Codon_usage) (codon prevelance)

In [10]:
seq = "ATG"
codons = pandas.read_csv(join(flat_files.ecoli_files_dir, "codon_usage.csv"), index_col=0)
for codon, row in codons.iterrows():
    if row.amino_acid == "Stop":
        continue
    seq += codon * int(row.per_1000 // 3)  # want roughly 300 aa
# get the most used stop codon
seq += codons[codons.amino_acid == "Stop"].sort_values("per_1000").index[-1]
building.add_dummy_reactions(me, seq, update=True)

# dummy proteins can be used to catalyze orphan reactions. This
# ensures that orphan reactions will not becore favored to fulfil 
# unmodeled protein fraction requirement 
rxn = cobrame.SummaryVariable('dummy_protein_to_mass')
me.add_reactions([rxn])
mass = me.metabolites.protein_dummy.formula_weight / 1000.  # in kDa
rxn.add_metabolites({'protein_biomass': -mass, 'protein_dummy': -1,
                     cobrame.Constraint('unmodeled_protein_biomass'): mass})

In [11]:
last = i+1;
reactionNumber = len(me.reactions);
for i in range(last,reactionNumber):
    rxn = me.reactions[i]
    print(i)
    print(rxn)
    print(rxn.reaction)

14372
transcription_RNA_dummy
220 atp_c + 250 ctp_c + 220 gtp_c + 222 utp_c --> RNA_dummy + 291.715403232 mRNA_biomass + 912 ppi_c
14373
DM_RNA_dummy
RNA_dummy + 291.715403232 mRNA_biomass --> 
14374
translation_dummy
0.000498399634202103*mu + 0.000195123456790123 + 0.00598079561042524*(mu + 0.3915)/mu RNA_dummy + 30 ala__L_c + 16 arg__L_c + 12 asn__L_c + 16 asp__L_c + 1.36212620027435*(mu + 0.3915)/mu atp_c + 3 cys__L_c + 14 gln__L_c + 18 glu__L_c + 22 gly_c + 7 his__L_c + 19 ile__L_c + 32 leu__L_c + 14 lys__L_c + 1.74469020314338*(mu + 0.3915)/mu mRNA_biomass + 10 met__L_c + 12 phe__L_c + 12 pro__L_c + 15 ser__L_c + 15 thr__L_c + 5 trp__L_c + 9 tyr__L_c + 22 val__L_c --> 1.36212620027435*(mu + 0.3915)/mu adp_c + 1.31577503429355*(mu + 0.3915)/mu amp_c + 1.49519890260631*(mu + 0.3915)/mu cmp_c + 1.31577503429355*(mu + 0.3915)/mu gmp_c + 302.0 - 1.36212620027435*(mu + 0.3915)/mu h2o_c + 1.36212620027435*(mu + 0.3915)/mu h_c + 1.36212620027435*(mu + 0.3915)/mu pi_c + 33.710405400000006 

### 6) Assocated Complexes and build Metabolic Reactions 
- Required
    * **enzyme_reaction_association.txt**
    * **reactions.txt** (gives reaction name, reversiblity, source and whether reaction is spontaneous)


In [12]:
# associate reaction id with the old ME complex id (including modifications)
rxn_to_cplx_dict = flat_files.get_reaction_to_complex(m_model)
rxn_info = flat_files.get_reaction_info_frame('reactions.txt')

# Required to add dummy reaction as spontaneous reaction
rxn_info = rxn_info.append(pandas.Series({'description': 'dummy reaction', 'is_reversible': 0,
                                          'is_spontaneous':1}, name='dummy_reaction'))

building.add_reactions_from_stoichiometric_data(me, rxn_to_cplx_dict, rxn_info, update=True)

/home/jt/UCSD/cobrame-master/cobrame/util/building.py:698 UserWarning: Reaction (CAT) cannot carry flux
/home/jt/UCSD/cobrame-master/cobrame/util/building.py:698 UserWarning: Reaction (DHPTDNR) cannot carry flux
/home/jt/UCSD/cobrame-master/cobrame/util/building.py:698 UserWarning: Reaction (DHPTDNRN) cannot carry flux
/home/jt/UCSD/cobrame-master/cobrame/util/building.py:698 UserWarning: Reaction (FHL) cannot carry flux
/home/jt/UCSD/cobrame-master/cobrame/util/building.py:698 UserWarning: Reaction (SPODM) cannot carry flux
/home/jt/UCSD/cobrame-master/cobrame/util/building.py:698 UserWarning: Reaction (SPODMpp) cannot carry flux
/home/jt/UCSD/cobrame-master/cobrame/util/building.py:698 UserWarning: Reaction (SUCASPtpp) cannot carry flux
/home/jt/UCSD/cobrame-master/cobrame/util/building.py:698 UserWarning: Reaction (SUCFUMtpp) cannot carry flux
/home/jt/UCSD/cobrame-master/cobrame/util/building.py:698 UserWarning: Reaction (SUCMALtpp) cannot carry flux
/home/jt/UCSD/cobrame-master/co

In [13]:
last = i+1;
reactionNumber = len(me.reactions);
for i in range(last,reactionNumber):
    rxn = me.reactions[i]
    print(i)
    print(rxn)
    print(rxn.reaction)

14377
12DGR120tipp_FWD_CPLX_dummy
12dgr120_p + 4.27350427350427e-6*mu CPLX_dummy --> 12dgr120_c
14378
12DGR140tipp_FWD_CPLX_dummy
12dgr140_p + 4.27350427350427e-6*mu CPLX_dummy --> 12dgr140_c
14379
12DGR141tipp_FWD_CPLX_dummy
12dgr141_p + 4.27350427350427e-6*mu CPLX_dummy --> 12dgr141_c
14380
12DGR160tipp_FWD_CPLX_dummy
12dgr160_p + 4.27350427350427e-6*mu CPLX_dummy --> 12dgr160_c
14381
12DGR161tipp_FWD_CPLX_dummy
12dgr161_p + 4.27350427350427e-6*mu CPLX_dummy --> 12dgr161_c
14382
12DGR180tipp_FWD_CPLX_dummy
12dgr180_p + 4.27350427350427e-6*mu CPLX_dummy --> 12dgr180_c
14383
12DGR181tipp_FWD_CPLX_dummy
12dgr181_p + 4.27350427350427e-6*mu CPLX_dummy --> 12dgr181_c
14384
12PPDRtex_REV_CPLX0-7533
12ppd__R_p + 4.27350427350427e-6*mu CPLX0-7533 --> 12ppd__R_e
14385
12PPDRtex_FWD_CPLX0-7533
12ppd__R_e + 4.27350427350427e-6*mu CPLX0-7533 --> 12ppd__R_p
14386
12PPDRtex_REV_CPLX0-7530
12ppd__R_p + 4.27350427350427e-6*mu CPLX0-7530 --> 12ppd__R_e
14387
12PPDRtex_FWD_CPLX0-7530
12ppd__R_e + 4.273

14648
ACACT4r_REV_CPLX0-1667
3odcoa_c + 4.27350427350427e-6*mu CPLX0-1667 + coa_c --> accoa_c + occoa_c
14649
ACACT4r_FWD_CPLX0-1667
4.27350427350427e-6*mu CPLX0-1667 + accoa_c + occoa_c --> 3odcoa_c + coa_c
14650
ACACT5r_REV_FADA-CPLX
3oddcoa_c + 4.27350427350427e-6*mu FADA-CPLX + coa_c --> accoa_c + dcacoa_c
14651
ACACT5r_FWD_FADA-CPLX
4.27350427350427e-6*mu FADA-CPLX + accoa_c + dcacoa_c --> 3oddcoa_c + coa_c
14652
ACACT5r_REV_CPLX0-1667
3oddcoa_c + 4.27350427350427e-6*mu CPLX0-1667 + coa_c --> accoa_c + dcacoa_c
14653
ACACT5r_FWD_CPLX0-1667
4.27350427350427e-6*mu CPLX0-1667 + accoa_c + dcacoa_c --> 3oddcoa_c + coa_c
14654
ACACT6r_REV_FADA-CPLX
3otdcoa_c + 4.27350427350427e-6*mu FADA-CPLX + coa_c --> accoa_c + ddcacoa_c
14655
ACACT6r_FWD_FADA-CPLX
4.27350427350427e-6*mu FADA-CPLX + accoa_c + ddcacoa_c --> 3otdcoa_c + coa_c
14656
ACACT6r_REV_CPLX0-1667
3otdcoa_c + 4.27350427350427e-6*mu CPLX0-1667 + coa_c --> accoa_c + ddcacoa_c
14657
ACACT6r_FWD_CPLX0-1667
4.27350427350427e-6*mu CPL

4.27350427350427e-6*mu CPLX0-7533 + agm_e --> agm_p
14893
AGMtex_REV_CPLX0-7530
4.27350427350427e-6*mu CPLX0-7530 + agm_p --> agm_e
14894
AGMtex_FWD_CPLX0-7530
4.27350427350427e-6*mu CPLX0-7530 + agm_e --> agm_p
14895
AGMtex_REV_G6700-MONOMER
4.27350427350427e-6*mu G6700-MONOMER + agm_p --> agm_e
14896
AGMtex_FWD_G6700-MONOMER
4.27350427350427e-6*mu G6700-MONOMER + agm_e --> agm_p
14897
AGMtex_REV_CPLX0-7534
4.27350427350427e-6*mu CPLX0-7534 + agm_p --> agm_e
14898
AGMtex_FWD_CPLX0-7534
4.27350427350427e-6*mu CPLX0-7534 + agm_e --> agm_p
14899
AGPR_REV_N-ACETYLGLUTPREDUCT-MONOMER
4.27350427350427e-6*mu N-ACETYLGLUTPREDUCT-MONOMER + acg5p_c + h_c + nadph_c --> acg5sa_c + nadp_c + pi_c
14900
AGPR_FWD_N-ACETYLGLUTPREDUCT-MONOMER
4.27350427350427e-6*mu N-ACETYLGLUTPREDUCT-MONOMER + acg5sa_c + nadp_c + pi_c --> acg5p_c + h_c + nadph_c
14901
AGt3_FWD_CPLX0-1721
4.27350427350427e-6*mu CPLX0-1721 + ag_c + h_e --> ag_e + h_c
14902
AHCYSNS_FWD_CPLX0-1541
4.27350427350427e-6*mu CPLX0-1541 + ahcys

4.27350427350427e-6*mu EG11829-MONOMER_mod_mn2 + bmoco1gdp_c + gtp_c + h_c --> bmocogdp_c + ppi_c
15219
BMOGDS2_FWD_EG11829-MONOMER_mod_mg2
4.27350427350427e-6*mu EG11829-MONOMER_mod_mg2 + bmoco1gdp_c + gtp_c + h_c --> bmocogdp_c + ppi_c
15220
BMOGDS2_FWD_EG11829-MONOMER_EG11828-MONOMER
4.27350427350427e-6*mu EG11829-MONOMER_EG11828-MONOMER + bmoco1gdp_c + gtp_c + h_c --> bmocogdp_c + ppi_c
15221
BPNT_FWD_EG10043-MONOMER_mod_mg2
4.27350427350427e-6*mu EG10043-MONOMER_mod_mg2 + h2o_c + pap_c --> amp_c + pi_c
15222
BSORx_FWD_EG10124-MONOMER_mod_bmocogdp
4.27350427350427e-6*mu EG10124-MONOMER_mod_bmocogdp + btnso_c + h_c + nadh_c --> btn_c + h2o_c + nad_c
15223
BSORy_FWD_EG10124-MONOMER_mod_bmocogdp
4.27350427350427e-6*mu EG10124-MONOMER_mod_bmocogdp + btnso_c + h_c + nadph_c --> btn_c + h2o_c + nadp_c
15224
BTNt2ipp_FWD_CPLX_dummy
4.27350427350427e-6*mu CPLX_dummy + btn_p + h_p --> btn_c + h_c
15225
BTNtex_REV_CPLX0-7533
4.27350427350427e-6*mu CPLX0-7533 + btn_p --> btn_e
15226
BTNtex_FW

4.27350427350427e-6*mu G6700-MONOMER + cyan_p --> cyan_e
15552
CYANtex_FWD_G6700-MONOMER
4.27350427350427e-6*mu G6700-MONOMER + cyan_e --> cyan_p
15553
CYANtex_REV_CPLX0-7534
4.27350427350427e-6*mu CPLX0-7534 + cyan_p --> cyan_e
15554
CYANtex_FWD_CPLX0-7534
4.27350427350427e-6*mu CPLX0-7534 + cyan_e --> cyan_p
15555
CYNTAH_FWD_CPLX0-7520
4.27350427350427e-6*mu CPLX0-7520 + cynt_c + 3.0 h_c + hco3_c --> 2.0 co2_c + nh4_c
15556
CYNTt2pp_FWD_CYNX-MONOMER
4.27350427350427e-6*mu CYNX-MONOMER + cynt_p + h_p --> cynt_c + h_c
15557
CYNTtex_REV_CPLX0-7533
4.27350427350427e-6*mu CPLX0-7533 + cynt_p --> cynt_e
15558
CYNTtex_FWD_CPLX0-7533
4.27350427350427e-6*mu CPLX0-7533 + cynt_e --> cynt_p
15559
CYNTtex_REV_CPLX0-7530
4.27350427350427e-6*mu CPLX0-7530 + cynt_p --> cynt_e
15560
CYNTtex_FWD_CPLX0-7530
4.27350427350427e-6*mu CPLX0-7530 + cynt_e --> cynt_p
15561
CYNTtex_REV_G6700-MONOMER
4.27350427350427e-6*mu G6700-MONOMER + cynt_p --> cynt_e
15562
CYNTtex_FWD_G6700-MONOMER
4.27350427350427e-6*mu 

...

PMANM_REV_PHOSMANMUT-MONOMER
4.27350427350427e-6*mu PHOSMANMUT-MONOMER + man6p_c --> man1p_c
18327
PMANM_FWD_PHOSMANMUT-MONOMER
4.27350427350427e-6*mu PHOSMANMUT-MONOMER + man1p_c --> man6p_c
18328
PMDPHT_FWD_CPLX_dummy
5aprbu_c + 4.27350427350427e-6*mu CPLX_dummy + h2o_c --> 4r5au_c + pi_c
18329
PMPK_FWD_HMP-P-KIN-CPLX
4ampm_c + 4.27350427350427e-6*mu HMP-P-KIN-CPLX + atp_c --> 2mahmp_c + adp_c
18330
PNTK_FWD_PANTOTHENATE-KIN-CPLX_mod_mg2
4.27350427350427e-6*mu PANTOTHENATE-KIN-CPLX_mod_mg2 + atp_c + pnto__R_c --> 4ppan_c + adp_c + h_c
18331
PNTOt4pp_FWD_PANF-MONOMER
4.27350427350427e-6*mu PANF-MONOMER + na1_p + pnto__R_p --> na1_c + pnto__R_c
18332
PNTOtex_REV_CPLX0-7533
4.27350427350427e-6*mu CPLX0-7533 + pnto__R_p --> pnto__R_e
18333
PNTOtex_FWD_CPLX0-7533
4.27350427350427e-6*mu CPLX0-7533 + pnto__R_e --> pnto__R_p
18334
PNTOtex_REV_CPLX0-7530
4.27350427350427e-6*mu CPLX0-7530 + pnto__R_p --> pnto__R_e
18335
PNTOtex_FWD_CPLX0-7530
4.27350427350427e-6*mu CPLX0-7530 + pnto__R_e --> p

PYDXNtex_REV_CPLX0-7534
4.27350427350427e-6*mu CPLX0-7534 + pydxn_p --> pydxn_e
18551
PYDXNtex_FWD_CPLX0-7534
4.27350427350427e-6*mu CPLX0-7534 + pydxn_e --> pydxn_p
18552
PYDXNtpp_FWD_CPLX_dummy
4.27350427350427e-6*mu CPLX_dummy + pydxn_p --> pydxn_c
18553
PYDXPP_FWD_EG11470-MONOMER_mod_mg2
4.27350427350427e-6*mu EG11470-MONOMER_mod_mg2 + h2o_c + pydx5p_c --> pi_c + pydx_c
18554
PYDXPP_FWD_EG11239-MONOMER_mod_mg2
4.27350427350427e-6*mu EG11239-MONOMER_mod_mg2 + h2o_c + pydx5p_c --> pi_c + pydx_c
18555
PYDXPP_FWD_G6246-MONOMER_mod_mg2
4.27350427350427e-6*mu G6246-MONOMER_mod_mg2 + h2o_c + pydx5p_c --> pi_c + pydx_c
18556
PYDXtex_REV_CPLX0-7533
4.27350427350427e-6*mu CPLX0-7533 + pydx_p --> pydx_e
18557
PYDXtex_FWD_CPLX0-7533
4.27350427350427e-6*mu CPLX0-7533 + pydx_e --> pydx_p
18558
PYDXtex_REV_CPLX0-7530
4.27350427350427e-6*mu CPLX0-7530 + pydx_p --> pydx_e
18559
PYDXtex_FWD_CPLX0-7530
4.27350427350427e-6*mu CPLX0-7530 + pydx_e --> pydx_p
18560
PYDXtex_REV_G6700-MONOMER
4.27350427350

4.27350427350427e-6*mu CPLX0-7534 + tmao_e --> tmao_p
18998
TMAtex_REV_CPLX0-7533
4.27350427350427e-6*mu CPLX0-7533 + tma_p --> tma_e
18999
TMAtex_FWD_CPLX0-7533
4.27350427350427e-6*mu CPLX0-7533 + tma_e --> tma_p
19000
TMAtex_REV_CPLX0-7530
4.27350427350427e-6*mu CPLX0-7530 + tma_p --> tma_e
19001
TMAtex_FWD_CPLX0-7530
4.27350427350427e-6*mu CPLX0-7530 + tma_e --> tma_p
19002
TMAtex_REV_G6700-MONOMER
4.27350427350427e-6*mu G6700-MONOMER + tma_p --> tma_e
19003
TMAtex_FWD_G6700-MONOMER
4.27350427350427e-6*mu G6700-MONOMER + tma_e --> tma_p
19004
TMAtex_REV_CPLX0-7534
4.27350427350427e-6*mu CPLX0-7534 + tma_p --> tma_e
19005
TMAtex_FWD_CPLX0-7534
4.27350427350427e-6*mu CPLX0-7534 + tma_e --> tma_p
19006
TMDK1_FWD_TDK-MONOMER_mod_mg2
4.27350427350427e-6*mu TDK-MONOMER_mod_mg2 + atp_c + thymd_c --> adp_c + dtmp_c + h_c
19007
TMDPP_REV_DEOA-CPLX
2dr1p_c + 4.27350427350427e-6*mu DEOA-CPLX + thym_c --> pi_c + thymd_c
19008
TMDPP_FWD_DEOA-CPLX
4.27350427350427e-6*mu DEOA-CPLX + pi_c + thymd_c

4.27350427350427e-6*mu CPLX0-7533 + ump_e --> ump_p
19217
UMPtex_REV_CPLX0-7530
4.27350427350427e-6*mu CPLX0-7530 + ump_p --> ump_e
19218
UMPtex_FWD_CPLX0-7530
4.27350427350427e-6*mu CPLX0-7530 + ump_e --> ump_p
19219
UMPtex_REV_G6700-MONOMER
4.27350427350427e-6*mu G6700-MONOMER + ump_p --> ump_e
19220
UMPtex_FWD_G6700-MONOMER
4.27350427350427e-6*mu G6700-MONOMER + ump_e --> ump_p
19221
UMPtex_REV_CPLX0-7534
4.27350427350427e-6*mu CPLX0-7534 + ump_p --> ump_e
19222
UMPtex_FWD_CPLX0-7534
4.27350427350427e-6*mu CPLX0-7534 + ump_e --> ump_p
19223
UPLA4FNF_FWD_G7169-MONOMER
4.27350427350427e-6*mu G7169-MONOMER + h2o_c + uLa4fn_c --> for_c + uLa4n_c
19224
UPLA4FNT_FWD_G7167-MONOMER
4.27350427350427e-6*mu G7167-MONOMER + udcpp_c + udpLa4fn_c --> uLa4fn_c + udp_c
19225
UPP3MT_FWD_HEMX-MONOMER
4.27350427350427e-6*mu HEMX-MONOMER + 2.0 amet_c + uppg3_c --> 2.0 ahcys_c + dscl_c + h_c
19226
UPP3MT_FWD_SIROHEMESYN-CPLX
4.27350427350427e-6*mu SIROHEMESYN-CPLX + 2.0 amet_c + uppg3_c --> 2.0 ahcys_c 

RED-THIOREDOXIN-MONOMER + 4.27350427350427e-6*mu RIBONUCLEOSIDE-DIP-REDUCTI-CPLX_mod_mg2_mod_fe2 + udp_c --> RED-THIOREDOXIN-MONOMER_mod_Oxidized + dudp_c + h2o_c
19550
RNDR42_FWD_RIBONUCLEOSIDE-DIP-REDUCTI-CPLX_mod_mg2_mod_fe2
RED-THIOREDOXIN2-MONOMER + 4.27350427350427e-6*mu RIBONUCLEOSIDE-DIP-REDUCTI-CPLX_mod_mg2_mod_fe2 + udp_c --> RED-THIOREDOXIN2-MONOMER_mod_Oxidized + dudp_c + h2o_c
19551
EDTXS11_FWD_LAUROYLACYLTRAN-MONOMER
EG50003-MONOMER_mod_pan4p_mod_ddca + 4.27350427350427e-6*mu LAUROYLACYLTRAN-MONOMER + kdo2lipid4_c --> EG50003-MONOMER_mod_pan4p + kdo2lipid4L_c
19552
AACPS71_FWD_AAS-MONOMER_mod_mg2
4.27350427350427e-6*mu AAS-MONOMER_mod_mg2 + EG50003-MONOMER_mod_pan4p + atp_c + ddca_c --> EG50003-MONOMER_mod_pan4p_mod_ddca + amp_c + ppi_c
19553
FA100ACPHi1_FWD_EG11095-MONOMER_mod_zn2_mod_fe2_mod_cobalt2_mod_mg2_mod_mn2
4.27350427350427e-6*mu EG11095-MONOMER_mod_zn2_mod_fe2_mod_cobalt2_mod_mg2_mod_mn2 + EG50003-MONOMER_mod_pan4p_mod_dca + h2o_c --> EG50003-MONOMER_mod_pan4p 

### 7) Incorporate remaining biomass constituents
There are leftover components from the *i*JO1366 biomass equation that either: 
1. have no mechanistic function in the model (glycogen)
2. are cofactors that are regenerated (nad)

Applies demands and coefficients from the *i*JO1366 biomass objective function

In [14]:
me.ngam = 1.
me.gam = 34.98
me.unmodeled_protein_fraction = .36

biomass_constituents = {
    "glycogen_c": -.023 / (me.metabolites.glycogen_c.formula_weight / 1000.),
    "2ohph_c": -0.000223,
    "nad_c": -.001831,
    "udcpdp_c": -5.5e-05,
    "coa_c": -0.000576,
    "ribflv_c": -0.000223,
    "nadp_c": -0.000447,
    "mlthf_c": -0.000223,
    "thf_c": -0.000223,
    "10fthf_c": -0.000223
}


rxn = cobrame.SummaryVariable('biomass_constituent_demand')
me.add_reactions([rxn])
rxn.add_metabolites(biomass_constituents)
constituent_mass = sum(me.metabolites.get_by_id(c).formula_weight / 1000. * -v
                     for c, v in biomass_constituents.items())
rxn.lower_bound = mu
rxn.upper_bound = mu
rxn.add_metabolites({me.metabolites.constituent_biomass: constituent_mass})

/home/jt/UCSD/cobrame-master/cobrame/core/model.py:103 UserWarning: Adding ATPM reaction to model
/home/jt/UCSD/cobrame-master/cobrame/core/model.py:86 UserWarning: Adding GAM reaction to model


 #### Lipid components
 Metabolites and coefficients from *i*JO1366 biomass objective function

In [15]:
# Find biomass constituents with 3 numbers followed by a compartment in the BOF
lipid = re.compile('\d{3}_.')
lipid_demand = {}
for key, value in ijo.reactions.Ec_biomass_iJO1366_core_53p95M.metabolites.items():
    if lipid.search(key.id):
        lipid_demand[key.id] = abs(value)
                
for met, requirement in lipid_demand.items():
    component_mass = me.metabolites.get_by_id(met).formula_weight / 1000.
    rxn = cobrame.SummaryVariable('Demand_' + met)
    me.add_reactions([rxn])
    rxn.add_metabolites({met: -1 * requirement,
                         'lipid_biomass': component_mass * requirement})
    rxn.lower_bound = mu
    rxn.upper_bound = 1000.

# Kdo2lipid4
requirement = 0.01945  # in mmol/gDW
met = me.metabolites.get_by_id('kdo2lipid4_e')
component_mass = met.formula_weight / 1000.
rxn = cobrame.SummaryVariable('Demand_' + met.id)
me.add_reactions([rxn])

rxn.add_metabolites({met.id : -1.*requirement,
                     'lipid_biomass': component_mass * requirement})
rxn.lower_bound = mu
rxn.upper_bound = mu

In [16]:
last = i+1;
reactionNumber = len(me.reactions);
for i in range(last,reactionNumber):
    rxn = me.reactions[i]
    print(i)
    print(rxn)
    print(rxn.reaction)

19643
ATPM
atp_c + h2o_c --> adp_c + h_c + pi_c
19644
GAM
34.98 atp_c + 34.98 h2o_c --> 34.98 adp_c + 34.98 h_c + 34.98 pi_c
19645
biomass_constituent_demand
0.000223 10fthf_c + 0.000223 2ohph_c + 0.000576 coa_c + 0.14185219494685478 glycogen_c + 0.000223 mlthf_c + 0.001831 nad_c + 0.000447 nadp_c + 0.000223 ribflv_c + 0.000223 thf_c + 5.5e-05 udcpdp_c --> 0.025570019438980993 constituent_biomass
19646
Demand_pe161_p
0.02106 pe161_p --> 0.014487750222659999 lipid_biomass
19647
Demand_pe160_p
0.045946 pe160_p --> 0.031792753773466 lipid_biomass
19648
Demand_pe160_c
0.017868 pe160_c --> 0.012363925574027998 lipid_biomass
19649
Demand_pe161_c
0.054154 pe161_c --> 0.037254018307594 lipid_biomass
19650
Demand_kdo2lipid4_e
0.01945 kdo2lipid4_e --> 0.0357882458869 lipid_biomass


#### DNA Demand Requirements
Added based on growth rate dependent DNA levels as in [O'brien EJ et al 2013](https://www.ncbi.nlm.nih.gov/pubmed/24084808)

In [17]:
dna_demand_stoich, dna_demand_bound = ecolime.dna_replication.return_gr_dependent_dna_demand(
    me, me.global_info['GC_fraction'])

dna_replication = cobrame.SummaryVariable("DNA_replication")
me.add_reaction(dna_replication)
dna_replication.add_metabolites(dna_demand_stoich)
dna_biomass = cobrame.Constraint("DNA_biomass")

dna_mw = 0
dna_mw_no_ppi = ecolime.dna_replication.get_dna_mw_no_ppi_dict(me)
for met, value in me.reactions.DNA_replication.metabolites.items():
    if met.id != 'ppi_c':
        dna_mw -= value * dna_mw_no_ppi[met.id.replace('_c','')] / 1000.
        
dna_replication.add_metabolites({dna_biomass: dna_mw})
dna_replication.lower_bound = dna_demand_bound 
dna_replication.upper_bound = dna_demand_bound 


**Note**: From this point forward, executing every codeblock should result in a solveable ME-model

------

## Part 2: Add metastructures to solving ME-model
This includes:
1. ribosome
2. RNA polymerase
3. charged_tRNAs

Sometimes multiple entities can perform the same role. To prevent a combinatorial explosion of possibilities, we can create  "generic" version, where any of those entities can fill in.

In [28]:
for generic, components in generics.generic_dict.items():
    cobrame.GenericData(generic, me, components).create_reactions()

ValueError: id generic_16Sm4Cm1402 is already present in list

### 1) Add ribosome
This uses the ribosome composition definition in **ecolime/ribosome.py**

In [29]:
ecolime.ribosome.add_ribosome(me, verbose=False)

ValueError: id ribosome is already present in list

In [30]:
last = 19652;
reactionNumber = len(me.reactions);
for i in range(last,reactionNumber):
    rxn = me.reactions[i]
    print(i)
    print(rxn)
    print(rxn.reaction)

19652
RsmH_mono_to_generic_16Sm4Cm1402
RsmH_mono --> generic_16Sm4Cm1402
19653
RsmI_mono_to_generic_16Sm4Cm1402
RsmI_mono --> generic_16Sm4Cm1402
19654
LysI_RS_dim_to_generic_LYSINEaaRS
LysI_RS_dim --> generic_LYSINEaaRS
19655
LysII_RS_dim_mod_6:mg2_to_generic_LYSINEaaRS
LysII_RS_dim_mod_6:mg2 --> generic_LYSINEaaRS
19656
DusA_mono_to_generic_Dus
DusA_mono --> generic_Dus
19657
DusB_mono_to_generic_Dus
DusB_mono --> generic_Dus
19658
DusC_mono_to_generic_Dus
DusC_mono --> generic_Dus
19659
PrfA_mono_to_generic_RF
PrfA_mono --> generic_RF
19660
PrfB_mono_to_generic_RF
PrfB_mono --> generic_RF
19661
TufA_mono_to_generic_Tuf
TufA_mono --> generic_Tuf
19662
TufB_mono_to_generic_Tuf
TufB_mono --> generic_Tuf
19663
RNase_T_dim_mod_4:mg2_to_generic_RNase
RNase_T_dim_mod_4:mg2 --> generic_RNase
19664
RNase_BN_dim_mod_2:zn2_to_generic_RNase
RNase_BN_dim_mod_2:zn2 --> generic_RNase
19665
Rnd_mono_mod_5:mg2_to_generic_RNase
Rnd_mono_mod_5:mg2 --> generic_RNase
19666
Rnb_mono_mod_1:mg2_to_generic_

### 2) Add charged tRNA reactions

The tRNA charging reactions were automatically added when loading the genome from the genbank file. However, the charging reactions still need to be made aware of the tRNA synthetases which are responsible.

Uses **trna_charging.py**

In [31]:
aa_synthetase_dict = ecolime.trna_charging.amino_acid_trna_synthetase
for data in me.tRNA_data:
    data.synthetase = str(aa_synthetase_dict[data.amino_acid])

Generic charged tRNAs are added to translation reactions via SubreactionData below.

All new data added in this block contained in **ecolime/translation.py**

In [32]:
ecolime.translation.add_charged_trna_subreactions(me)
for data in me.translation_data:
    data.add_initiation_subreactions(start_codons=translation.translation_start_codons,
                                    start_subreactions=set(translation.initiation_subreactions.keys()))

    data.add_elongation_subreactions(elongation_subreactions=set(translation.elongation_subreactions.keys()))

    data.add_termination_subreactions(translation_terminator_dict=translation.translation_stop_dict)

ValueError: id phe_addition_at_UUU is already present in list

In [33]:
last = i+1;
reactionNumber = len(me.reactions);
for i in range(last,reactionNumber):
    rxn = me.reactions[i]
    print(i)
    print(rxn)
    print(rxn.reaction)

### 3) Add Transcription Metacomplexes
#### RNA Polymerase

Data for RNA_polymerase composition fround in **ecolime/transcription**

Uses *tu_df* from **TUs_from_ecocyc.txt**, above

In [34]:
for met in transcription.rna_polymerases:
    rnap_obj = cobrame.RNAP(met)
    me.add_metabolites(rnap_obj)
transcription.add_rna_polymerase_complexes(me, verbose=False)

# associate the correct RNA_polymerase and factors to TUs
sigma_to_rnap_dict = transcription.sigma_factor_complex_to_rna_polymerase_dict
for tu_id in tu_df.index:
    transcription_data = me.process_data.get_by_id(tu_id)
    sigma = tu_df.sigma[tu_id]
    rna_polymerase = sigma_to_rnap_dict[sigma]
    transcription_data.RNA_polymerase = rna_polymerase

#### Degradosome (both for RNA degradation and RNA splicing)

All new data contained in **transcription.py**

In [35]:
me.add_metabolites([cobrame.Complex('RNA_degradosome')])
data = cobrame.ComplexData('RNA_degradosome', me)
for subunit, value in transcription.rna_degradosome.items():
    data.stoichiometry[subunit] = value
data.create_complex_formation(verbose=False)

# Used for RNA splicing
data = cobrame.SubreactionData('RNA_degradation_machine', me)
data.enzyme = 'RNA_degradosome'

data = cobrame.SubreactionData('RNA_degradation_atp_requirement', me)
# .25 water equivaltent for atp hydrolysis per nucleotide
data.stoichiometry = {'atp_c': -.25, 'h2o_c': -.25, 'adp_c': .25,
                      'pi_c': .25, 'h_c': .25}

transcription.add_rna_splicing(me)

In [36]:
last = i+1;
reactionNumber = len(me.reactions);
for i in range(last,reactionNumber):
    rxn = me.reactions[i]
    print(i)
    print(rxn)
    print(rxn.reaction)

19691
formation_CPLX0-221
FecI_mono + hRNAP_mod_1:zn2_mod_2:mg2 --> CPLX0-221
19692
formation_RNAPE-CPLX
RpoE_mono + hRNAP_mod_1:zn2_mod_2:mg2 --> RNAPE-CPLX
19693
formation_CPLX0-222
FliA_mono + hRNAP_mod_1:zn2_mod_2:mg2 --> CPLX0-222
19694
formation_RNAP32-CPLX
RpoH_mono + hRNAP_mod_1:zn2_mod_2:mg2 --> RNAP32-CPLX
19695
formation_RNAP54-CPLX
RpoN_mono + hRNAP_mod_1:zn2_mod_2:mg2 --> RNAP54-CPLX
19696
formation_RNAP70-CPLX
RpoD_mono + hRNAP_mod_1:zn2_mod_2:mg2 --> RNAP70-CPLX
19697
formation_RNAPS-CPLX
RpoS_mono + hRNAP_mod_1:zn2_mod_2:mg2 --> RNAPS-CPLX
19698
formation_RNA_degradosome
Eno_dim_mod_4:mg2 + Orn_dim_mod_2:mg2 + Pnp_trim + RNase_E_tetra_mod_2:zn2 + RhlB_dim --> RNA_degradosome
19699
formation_rRNA_containing_excision_machinery
RNase_E_tetra_mod_2:zn2 + RNase_G_dim + RNase_III_dim_mod_2:mg2 + RNase_P_cplx_mod_2:mg2 + RNase_T_dim_mod_4:mg2 + RNase_m16 + RNase_m23 + RNase_m5 + generic_RNase --> rRNA_containing_excision_machinery
19700
formation_monocistronic_excision_machine

------
## Part 3: Add remaining modifications
rRNA modifications handled in *add_ribosome*

### 1) Add complex modifications
*complex_modification_dict* from **protein_modification.text**, above

The rest of the new data contained in **ecolime/modifications.py**

In [37]:
for complex_id, info in complex_modification_dict.items():
    modifications = {}
    for mod, value in info['modifications'].items():
        # stoichiometry of modification determined in 
        # subreaction_data.stoichiometry
        modifications['mod_' + mod] = abs(value)
    me.process_data.get_by_id(complex_id).subreactions = modifications

# Adds modification data for more complicated enzyme modifications
# (ie, iron sulfur cluster modification)
ecolime.modifications.add_modification_procedures(me)

# add formation reactions for each of the ComplexDatas
for cplx_data in me.complex_data:
    formation = cplx_data.formation
    if formation:
        formation.update()
    else:
        cplx_data.create_complex_formation()

### 2) Add tRNA mods and asocciate them with tRNA charging reactions
New data from:
1. **ecolime/trna_charging.py** (read via *add_tRNA_modification_procedures()*)
2. **post_transcriptional_modification_of_tRNA.txt** (modification types per tRNA)


In [38]:
# Add tRNA modifications to ME-model
ecolime.trna_charging.add_trna_modification_procedures(me)

# trna_modifications = {tRNA_id: {modifications: count}}
trna_modifications=flat_files.get_trna_modification_targets()
for trna in trna_modifications:
    for data in me.process_data.query(trna):
        data.subreactions = trna_modifications[trna]

In [39]:
last = i+1;
reactionNumber = len(me.reactions);
for i in range(last,reactionNumber):
    rxn = me.reactions[i]
    print(i)
    print(rxn)
    print(rxn.reaction)

19702
CPLX0-7617_mod_1:2fe2s_to_generic_2fe2s_transfer_complex
CPLX0-7617_mod_1:2fe2s --> generic_2fe2s_transfer_complex
19703
CPLX0-7824_mod_1:2fe2s_to_generic_2fe2s_transfer_complex
CPLX0-7824_mod_1:2fe2s --> generic_2fe2s_transfer_complex
19704
IscA_tetra_mod_1:2fe2s_to_generic_2fe2s_transfer_complex
IscA_tetra_mod_1:2fe2s --> generic_2fe2s_transfer_complex
19705
CPLX0-7617_mod_1:4fe4s_to_generic_4fe4s_transfer_complex
CPLX0-7617_mod_1:4fe4s --> generic_4fe4s_transfer_complex
19706
CPLX0-7824_mod_1:4fe4s_to_generic_4fe4s_transfer_complex
CPLX0-7824_mod_1:4fe4s --> generic_4fe4s_transfer_complex
19707
IscA_tetra_mod_1:4fe4s_to_generic_4fe4s_transfer_complex
IscA_tetra_mod_1:4fe4s --> generic_4fe4s_transfer_complex
19708
CPLX0-7617_2fe2s_c_unloading
CPLX0-7617_mod_1:2fe2s --> 2fe2s_c + CPLX0-7617
19709
IscA_tetra_2fe2s_c_unloading
IscA_tetra_mod_1:2fe2s --> 2fe2s_c + IscA_tetra
19710
CPLX0-7824_2fe2s_c_unloading
CPLX0-7824_mod_1:2fe2s --> 2fe2s_c + CPLX0-7824
19711
CPLX0-7617_4fe4s_c_

---
## Part 4: Add remaining subreactions
### 1) Add translation related subreactions
All new data from **ecolime/translation.py**

In [40]:
# add the translation subreaction data objects to model
translation.add_translation_subreactions_to_model(me)

# add translation subreaction data to reactions
methionine_cleaved=translation.methionine_cleaved
folding_dict=translation.folding_dict

for data in me.translation_data:
    locus_id = data.id
    if locus_id in methionine_cleaved:
        data.subreactions['N_terminal_methionine_cleavage'] = 1

    for folding_type in folding_dict:
        if locus_id in folding_dict[folding_type]:
            data.subreactions[folding_type] = 1

    # This block was ran above, but should be ran again to 
    # incorporate any subreactions not added previously
    data.add_initiation_subreactions(
        start_codons=translation.translation_start_codons,
        start_subreactions=set(translation.initiation_subreactions.keys()))
    data.add_elongation_subreactions(
        elongation_subreactions=set(translation.elongation_subreactions.keys()))
    data.add_termination_subreactions(
        translation_terminator_dict=translation.translation_stop_dict)

    # add organism specific subreactions associated with peptide processing
    for subrxn in translation.peptide_processing_subreactions:
        data.subreactions[subrxn] = 1

Adding selenocystein for b1474
Adding selenocystein for b3894
Adding selenocystein for b4079


In [46]:
last = i+1;
reactionNumber = len(me.reactions);
for i in range(last,reactionNumber):
    rxn = me.reactions[i]
    print(i)
    print(rxn)
    print(rxn.reaction)

### 2) Add transcription related subreactions
All new data from **ecolime/transcription.py**

In [43]:
for subreaction in transcription.transcription_subreactions:
    subreaction_data = cobrame.SubreactionData(subreaction, me)
    enzymes = transcription.transcription_subreactions[subreaction]['enzymes']
    subreaction_data.stoichiometry = transcription.transcription_subreactions[subreaction]['stoich']
    subreaction_data.enzyme = enzymes

for transcription_data in me.transcription_data:
    # Assume false if not in tu_df
    rho_dependent = tu_df.rho_dependent.get(transcription_data.id, False)
    rho = 'dependent' if rho_dependent else 'independent'
    stable = 'stable' if transcription_data.codes_stable_rna else 'normal'
    transcription_data.subreactions['Transcription_%s_rho_%s' % (stable,
                                                                 rho)] = 1

In [44]:
last = i+1;
reactionNumber = len(me.reactions);
for i in range(last,reactionNumber):
    rxn = me.reactions[i]
    print(i)
    print(rxn)
    print(rxn.reaction)

----
## Part 5: Add in translocation

New data from:
1. **peptide_compartment_and_pathways.txt** (Protein compartment and translocation pathway for each membrane complex)
2. **ecolime/translocation.py** (definitions of each translocation pathway)

In [47]:
# Add TranslocationData
transloc = pandas.read_csv(join(flat_files.ecoli_files_dir,"peptide_compartment_and_pathways2.txt"),
                           sep='\t', comment="#")
for pathway, info in ecolime.translocation.pathway.items():
    if 'alt' not in pathway:
        transloc_data = cobrame.TranslocationData(pathway + '_translocation', me)
    else:
        transloc_data = cobrame.TranslocationData(pathway.replace('_alt', '_translocation_alt'), me)
    transloc_data.enzyme_dict = info['enzymes']
    transloc_data.keff = info['keff']
    transloc_data.length_dependent_energy = info['length_dependent_energy']
    transloc_data.stoichiometry = info['stoichiometry']

# Associate data and add translocation reactions
ecolime.translocation.add_translocation_pathways(me, transloc, membrane_constraints = False)

# Update stoichiometry of membrane complexes
# new_stoich = {complex_id: protein_w_compartment}
new_stoich = defaultdict(dict)
for cplx, row in transloc.set_index('Complex').iterrows():
    if cplx == 'EG10544-MONOMER':
        continue
    protein = row.Protein.split('(')[0] + '_' + row.Protein_compartment
    value = me.process_data.get_by_id(cplx).stoichiometry['protein_' + row.Protein.split('(')[0]]
    new_stoich[cplx]['protein_' + protein] = float(value)

for cplx, stoich in new_stoich.items():
    complex_data = me.process_data.get_by_id(cplx)
    for met, value in stoich.items():
        complex_data.stoichiometry.pop(met[0:13])
        complex_data.stoichiometry[met] = value
        complex_data.formation.update()
    # Complex ids in protein compartment file doesn't include mods
    # Some have multiple alternative modifications so must loop through these
    for complex_data in me.process_data.query(cplx + '_mod_'):
        for met, value in stoich.items():
            complex_data.stoichiometry.pop(met[0:13])
            complex_data.stoichiometry[met] = value
            complex_data.formation.update()

In [48]:
last = i+1;
reactionNumber = len(me.reactions);
for i in range(last,reactionNumber):
    rxn = me.reactions[i]
    print(i)
    print(rxn)
    print(rxn.reaction)

19717
translocation_b0007
0.00661111111111111*mu SRP-CPLX + 0.00661111111111111*mu Sec-CPLX + 0.00661111111111111*mu YidC_MONOMER + gtp_c + h2o_c + protein_b0007 --> gdp_c + h_c + pi_c + protein_b0007_Inner_Membrane
19718
translocation_b0019
4.27350427350427e-6*mu FtsY_MONOMER + 0.00538888888888889*mu SRP-CPLX + 0.00538888888888889*mu Sec-CPLX + 2.0 gtp_c + 2.0 h2o_c + protein_b0019 --> 2.0 gdp_c + 2.0 h_c + 2.0 pi_c + protein_b0019_Inner_Membrane
19719
translocation_b0027
4.27350427350427e-6*mu FtsY_MONOMER + 0.00227777777777778*mu SRP-CPLX + 0.00227777777777778*mu Sec-CPLX + 2.0 gtp_c + 2.0 h2o_c + protein_b0027 --> 2.0 gdp_c + 2.0 h_c + 2.0 pi_c + protein_b0027_Inner_Membrane
19720
translocation_b0040
4.27350427350427e-6*mu FtsY_MONOMER + 0.007*mu SRP-CPLX + 0.007*mu Sec-CPLX + 2.0 gtp_c + 2.0 h2o_c + protein_b0040 --> 2.0 gdp_c + 2.0 h_c + 2.0 pi_c + protein_b0040_Inner_Membrane
19721
translocation_b0047
4.27350427350427e-6*mu FtsY_MONOMER + 0.00861111111111111*mu SRP-CPLX + 0.0086

4.27350427350427e-6*mu FtsY_MONOMER + 0.000958333333333333*mu SRP-CPLX + 0.000958333333333333*mu Sec-CPLX + 2.0 gtp_c + 2.0 h2o_c + protein_b2198 --> 2.0 gdp_c + 2.0 h_c + 2.0 pi_c + protein_b2198_Inner_Membrane
19956
translocation_b2199
0.00340277777777778*mu SRP-CPLX + 0.00340277777777778*mu Sec-CPLX + 0.00340277777777778*mu YidC_MONOMER + gtp_c + h2o_c + protein_b2199 --> gdp_c + h_c + pi_c + protein_b2199_Inner_Membrane
19957
translocation_b2200
4.27350427350427e-6*mu FtsY_MONOMER + 0.00305555555555556*mu SRP-CPLX + 0.00305555555555556*mu Sec-CPLX + 2.0 gtp_c + 2.0 h2o_c + protein_b2200 --> 2.0 gdp_c + 2.0 h_c + 2.0 pi_c + protein_b2200_Inner_Membrane
19958
translocation_b2202
4.27350427350427e-6*mu FtsY_MONOMER + 0.00277777777777778*mu SRP-CPLX + 0.00277777777777778*mu Sec-CPLX + 2.0 gtp_c + 2.0 h2o_c + protein_b2202 --> 2.0 gdp_c + 2.0 h_c + 2.0 pi_c + protein_b2202_Inner_Membrane
19959
translocation_b2203
0.0103472222222222*mu Sec-CPLX + 0.0103472222222222*mu SecA_MONOMER + 0.01

translocation_b3127
4.27350427350427e-6*mu FtsY_MONOMER + 0.00616666666666667*mu SRP-CPLX + 0.00616666666666667*mu Sec-CPLX + 2.0 gtp_c + 2.0 h2o_c + protein_b3127 --> 2.0 gdp_c + 2.0 h_c + 2.0 pi_c + protein_b3127_Inner_Membrane
20062
translocation_b3161
4.27350427350427e-6*mu FtsY_MONOMER + 0.00575*mu SRP-CPLX + 0.00575*mu Sec-CPLX + 2.0 gtp_c + 2.0 h2o_c + protein_b3161 --> 2.0 gdp_c + 2.0 h_c + 2.0 pi_c + protein_b3161_Inner_Membrane
20063
translocation_b3175
4.27350427350427e-6*mu FtsY_MONOMER + 0.00152777777777778*mu SRP-CPLX + 0.00152777777777778*mu Sec-CPLX + 2.0 gtp_c + 2.0 h2o_c + protein_b3175 --> 2.0 gdp_c + 2.0 h_c + 2.0 pi_c + protein_b3175_Inner_Membrane
20064
translocation_b3182
0.033125*mu Sec-CPLX + 0.033125*mu SecA_MONOMER + 0.033125*mu SecB_tetra + 19.080000000000002 atp_c + 19.080000000000002 h2o_c + protein_b3182 --> 19.080000000000002 adp_c + 19.080000000000002 h_c + 19.080000000000002 pi_c + protein_b3182_Periplasm
20065
translocation_b3196
4.27350427350427e-6*m

20164
translocation_b4067
4.27350427350427e-6*mu FtsY_MONOMER + 0.007625*mu SRP-CPLX + 0.007625*mu Sec-CPLX + 2.0 gtp_c + 2.0 h2o_c + protein_b4067 --> 2.0 gdp_c + 2.0 h_c + 2.0 pi_c + protein_b4067_Inner_Membrane
20165
translocation_b4070
0.0331944444444445*mu Sec-CPLX + 0.0331944444444445*mu SecA_MONOMER + 0.0331944444444445*mu SecB_tetra + 19.12 atp_c + 19.12 h2o_c + protein_b4070 --> 19.12 adp_c + 19.12 h_c + 19.12 pi_c + protein_b4070_Periplasm
20166
translocation_b4071
0.0130555555555556*mu Sec-CPLX + 0.0130555555555556*mu SecA_MONOMER + 0.0130555555555556*mu SecB_tetra + 7.5200000000000005 atp_c + 7.5200000000000005 h2o_c + protein_b4071 --> 7.5200000000000005 adp_c + 7.5200000000000005 h_c + 7.5200000000000005 pi_c + protein_b4071_Periplasm
20167
translocation_b4072
0.444444444444444*mu TatA_MONOMER + 0.0222222222222222*mu TatBC_octa + protein_b4072 --> protein_b4072_Periplasm
20168
translocation_b4072_alt
0.0222222222222222*mu TatBC_octa + 0.444444444444444*mu TatE_MONOMER + p

---
## Part 6: Add Cell Wall Components
All new data from **ecolime/translocation.py**

In [49]:
compartment_dict = {}
for prot, compartment in transloc.set_index('Protein').Protein_compartment.to_dict().items():
    compartment_dict[prot.split('(')[0]] = compartment

#### Add lipid modification SubreactionData

In [50]:
lipid_modifications = ecolime.translocation.lipid_modifications

for lipid in lipid_modifications:
    data = cobrame.SubreactionData('mod_' + lipid, me)
    data.stoichiometry = {lipid: -1, 'g3p_c': 1}
    data.enzyme = ['Lgt_MONOMER', 'LspA_MONOMER']
    # The element contribution is based on the lipid involved in the 
    # modification, so calculate based on the metabolite formula
    data._element_contribution = data.calculate_element_contribution()

data = cobrame.SubreactionData('mod2_pg160_p', me)
data.stoichiometry = {'pg160_p': -1, '2agpg160_p': 1}
data.enzyme = 'EG10168-MONOMER'
data._element_contribution = data.calculate_element_contribution()

data = cobrame.SubreactionData('mod2_pe160_p', me)
data.stoichiometry = {'pe160_p': -1, '2agpe160_p': 1}
data.enzyme = 'EG10168-MONOMER'
data._element_contribution = data.calculate_element_contribution()
    
ecolime.translocation.add_lipoprotein_formation(me, compartment_dict, 
                                                membrane_constraints=False)

#### Correct complex formation IDs if they contain lipoproteins

In [51]:
for gene in ecolime.translocation.lipoprotein_precursors.values():
    compartment = compartment_dict.get(gene)
    for rxn in me.metabolites.get_by_id('protein_' + gene + '_' + compartment).reactions:
        if isinstance(rxn, cobrame.ComplexFormation):
            data = me.process_data.get_by_id(rxn.complex_data_id)
            value = data.stoichiometry.pop('protein_' + gene + '_' + compartment)
            data.stoichiometry['protein_' + gene + '_lipoprotein' + '_' + compartment] = value
            rxn.update()

#### Braun's lipoprotein demand
Metabolites and coefficients as defined in [Liu et al 2014](http://bmcsystbiol.biomedcentral.com/articles/10.1186/s12918-014-0110-6)

In [52]:
rxn = cobrame.SummaryVariable('core_structural_demand_brauns')
met1 = me.metabolites.get_by_id('murein5px4p_p')
met1_mass = met1.formula_weight / 1000.
met2 = me.metabolites.get_by_id('protein_b1677_lipoprotein_Outer_Membrane')
me.add_reactions([rxn])
# biomass of lipoprotein accounted for in translation and lipid modification
rxn.add_metabolites({met1 : -0.013894, met2: -0.003597, 'peptidoglycan_biomass':(0.013894 * met1_mass)},
                    combine=False)
rxn.lower_bound = mu
rxn.upper_bound = mu

In [53]:
last = i+1;
reactionNumber = len(me.reactions);
for i in range(last,reactionNumber):
    rxn = me.reactions[i]
    print(i)
    print(rxn)
    print(rxn.reaction)

20203
b0463_lipid_modification_pg120_p_pg160
4.27350427350427e-6*mu EG10168-MONOMER + 4.27350427350427e-6*mu Lgt_MONOMER + 4.27350427350427e-6*mu LspA_MONOMER + pg120_p + pg160_p + protein_b0463_Inner_Membrane --> 2agpg160_p + g3p_c + 0.68011612 lipid_biomass + protein_b0463_lipoprotein_Inner_Membrane
20204
b0463_lipid_modification_pg120_p_pe160
4.27350427350427e-6*mu EG10168-MONOMER + 4.27350427350427e-6*mu Lgt_MONOMER + 4.27350427350427e-6*mu LspA_MONOMER + pe160_p + pg120_p + protein_b0463_Inner_Membrane --> 2agpe160_p + g3p_c + 0.68011612 lipid_biomass + protein_b0463_lipoprotein_Inner_Membrane
20205
b0463_lipid_modification_pg141_p_pg160
4.27350427350427e-6*mu EG10168-MONOMER + 4.27350427350427e-6*mu Lgt_MONOMER + 4.27350427350427e-6*mu LspA_MONOMER + pg141_p + pg160_p + protein_b0463_Inner_Membrane --> 2agpg160_p + g3p_c + 0.73219068 lipid_biomass + protein_b0463_lipoprotein_Inner_Membrane
20206
b0463_lipid_modification_pg141_p_pe160
4.27350427350427e-6*mu EG10168-MONOMER + 4.273

20329
b1209_lipid_modification_pg120_p_pg160
4.27350427350427e-6*mu EG10168-MONOMER + 4.27350427350427e-6*mu Lgt_MONOMER + 4.27350427350427e-6*mu LspA_MONOMER + pg120_p + pg160_p + protein_b1209_Outer_Membrane --> 2agpg160_p + g3p_c + 0.68011612 lipid_biomass + protein_b1209_lipoprotein_Outer_Membrane
20330
b1209_lipid_modification_pg120_p_pe160
4.27350427350427e-6*mu EG10168-MONOMER + 4.27350427350427e-6*mu Lgt_MONOMER + 4.27350427350427e-6*mu LspA_MONOMER + pe160_p + pg120_p + protein_b1209_Outer_Membrane --> 2agpe160_p + g3p_c + 0.68011612 lipid_biomass + protein_b1209_lipoprotein_Outer_Membrane
20331
b1209_lipid_modification_pg141_p_pg160
4.27350427350427e-6*mu EG10168-MONOMER + 4.27350427350427e-6*mu Lgt_MONOMER + 4.27350427350427e-6*mu LspA_MONOMER + pg141_p + pg160_p + protein_b1209_Outer_Membrane --> 2agpg160_p + g3p_c + 0.73219068 lipid_biomass + protein_b1209_lipoprotein_Outer_Membrane
20332
b1209_lipid_modification_pg141_p_pe160
4.27350427350427e-6*mu EG10168-MONOMER + 4.273

-----
## Part 7: Set keffs

Either entirely based on SASA or using fit keffs from [Ebrahim et al 2016](https://www.ncbi.nlm.nih.gov/pubmed/27782110?dopt=Abstract)

In [54]:
keff_list = []
keffs = flat_files.get_reaction_keffs(me, verbose=True)
for reaction_id, keff in keffs.items():
    if keff > 3000:
        keff = 3000.
    elif keff < .01:
        keff = .01
    keff_list.append(keff)
    me.reactions.get_by_id(reaction_id).keff = keff
    me.reactions.get_by_id(reaction_id).update()

# Keffs that were not set in the above block
me.process_data.N_terminal_methionine_cleavage.keff = 1339.4233102860871
me.process_data.peptide_deformylase_processing.keff = 1019.5963333345715
me.reactions.get_by_id('GLUTRR_FWD_CPLX0-3741').keff = 3000 # 3269.0108007383374
me.process_data.fmet_addition_at_START.keff = 1540.4356849968603
me.process_data.ribosome_recycler.keff = 1059.6910912619182
me.process_data.UAG_PrfA_mono_mediated_termination.keff = 1721.7910609284945
me.process_data.UGA_PrfB_mono_mediated_termination.keff = 1700.2966587695353
me.process_data.UAA_generic_RF_mediated_termination.keff = 1753.4238515034572

no keff found for keff_GLUTRR_CPLX0_DASH_3741
no keff found for keff_CU2R_NADH_DASH_DHII_DASH_MONOMER_mod_mg2_mod_cu_mod_fad


-----
## Part 8: Model updates and corrections

In [55]:
# Add reaction subsystems from iJO to model
for rxn in ijo.reactions:
    if rxn.id in me.process_data:
        data = me.process_data.get_by_id(rxn.id)
    else:
        continue
    for r in data.parent_reactions:
        r.subsystem = rxn.subsystem

#### Corrections and final updates

In [56]:
ecolime.corrections.correct_reaction_stoichiometries(me, join(flat_files.ecoli_files_dir, 
                                                              'iJL1678b_model_changes.xlsx'))
# RNA_dummy, TU_b3247, TU_b3705 do not have RNAP, this is set as the most common RNAP
for data in me.transcription_data:
    if len(data.RNA_polymerase) == 0:
        data.RNA_polymerase = 'RNAP70-CPLX'
        
# If lower_bound open, model feeds G6P into EDD
me.reactions.EX_pqq_e.lower_bound = 0
me.reactions.EX_pqq_e.upper_bound = 0

# cobalamin is not in glucose M9 media
me.reactions.EX_cbl1_e.lower_bound = 0

me.process_data.PPKr.lower_bound = 0.
me.process_data.PPKr.update_parent_reactions()
    

# This enyzme is involved in catalyzing this reaction
sub = cobrame.SubreactionData('EG12450-MONOMER_activity', me)
sub.enzyme = 'EG12450-MONOMER'
me.process_data.NHFRBO.subreactions['EG12450-MONOMER_activity'] = 1

#### Add enzymatic coupling for "carriers"
These are enzyme complexes that act as metabolites in a metabolic reaction (i.e. are metabolites in iJO1366)

In [57]:
for data in me.stoichiometric_data:
    if data.id == 'dummy_reaction':
        continue
        
    for met, value in data.stoichiometry.items():
        if not isinstance(me.metabolites.get_by_id(met), cobrame.Complex) or value > 0:
            continue
            
        subreaction_id = met + '_carrier_activity'
        if subreaction_id not in me.process_data:           
            sub = cobrame.SubreactionData(met + '_carrier_activity', me)
            sub.enzyme = met
        data.subreactions[subreaction_id] = abs(value)

----
## Part 9: Update and save

In [58]:
me.reactions.dummy_reaction_FWD_SPONT.objective_coefficient = 1.
me.reactions.EX_glc__D_e.lower_bound = -1000
me.reactions.EX_o2_e.lower_bound = -1000
me.ngam = 1.
me.gam = 34.98
me.unmodeled_protein_fraction = .36

In [59]:
me.update()
me.prune()

/home/jt/UCSD/cobrame-master/cobrame/core/processdata.py:256 UserWarning: met (generic_tRNA_GAG_glu__L_c) does not have formula


### Add remaining complex formulas and compartments to model

In [60]:
# Update a second time to incorporate all of the metabolite formulas corectly
for r in me.reactions.query('formation_'):
    r.update()

# Update complex formulas
df = pandas.read_table(join(flat_files.ecoli_files_dir, 'modification.txt'),
                            names=['mod', 'formula','na'])
df = df.drop('na', axis=1).set_index('mod').dropna(how='any')
modification_formulas = df.T.to_dict()
formulas.add_remaining_complex_formulas(me, modification_formulas)

me.metabolites.get_by_id('CPLX0-782_mod_1:2fe2s_mod_1:4fe4s').formula = 'C3164Fe6H5090N920O920S50'
me.metabolites.get_by_id('EG50003-MONOMER_mod_pan4p_mod_lipo').formula = 'C387H606N95O142PS4'
# Update reactions affected by formula update 
for r in me.reactions.query('_mod_lipo'):
    r.update()
for r in me.reactions.query('_mod_glycyl'):
    r.update()
    
# add metaboolite compartments
compartments.add_compartments_to_model(me)

In [61]:
n_genes = len(me.metabolites.query(re.compile('RNA_b[0-9]')))
print("number of genes in the model %d (%.2f%%)" % (n_genes, n_genes * 100. / (1678)))

number of genes in the model 1678 (100.00%)


In [62]:
with open("./me_models/iJL1678b.pickle", "wb") as outfile:
    pickle.dump(me, outfile)

In [ ]:
save_json_me_model(me, './me_models/iJL1678b.json')